In [183]:
import pandas as pd
import xml.etree.ElementTree as etree


tree = etree.parse("muni-fi-spr16.xml")
root = tree.getroot()

columns_problem = ["Name", "NrDays", "SlotsPerDay", "NrWeeks"]
columns_optimization = ["Time", "Room", "Distribution", "Student"]
columns_rooms = ["RoomId", "Capacity", "PreviousRoomIdList", "TravelTimeValueList", "UnavailableDaysList", "UnavailableStartList", "UnavailableLengthList", "UnavailableWeeksList"]
columns_courses = ["CourseId", "ConfigIdList"]
columns_configs = ["ConfigId", "SubpartIdList"]
columns_subparts = ["SubpartId", "ClassIdList"]
columns_classes = ["ClassId", "ClassLimit", "ClassParent"]
columns_distributions = ["DistributionId", "DistributionType", "DistributionRequired", "DistributionPenalty", "ClassesList"]
columns_students = ["StudentId", "CoursesList"]
columns_relation_class_room = ["ClassId", "RoomId", "RoomPenalty"]
columns_relation_class_time = ["ClassId", "TimeDays", "TimeStart", "TimeLength", "TimeWeeks", "TimePenalty"]

df_problem = pd.DataFrame(columns = columns_problem)
df_optimization = pd.DataFrame(columns = columns_optimization)
df_rooms = pd.DataFrame(columns = columns_rooms)
df_courses = pd.DataFrame(columns = columns_courses)
df_configs = pd.DataFrame(columns = columns_configs)
df_subparts = pd.DataFrame(columns = columns_subparts)
df_classes = pd.DataFrame(columns = columns_classes)
df_distributions = pd.DataFrame(columns = columns_distributions)
df_students = pd.DataFrame(columns = columns_students)
df_relation_class_room = pd.DataFrame(columns = columns_relation_class_room)
df_relation_class_time = pd.DataFrame(columns = columns_relation_class_time)




df_problem = df_problem.append({"Name": root.attrib.get("name"), "NrDays": root.attrib.get("nrDays"), "SlotsPerDay": root.attrib.get("slotsPerDay"), "NrWeeks": root.attrib.get("nrWeeks")}, ignore_index = True)

for node in root:
    if node.tag == "optimization":
        df_optimization = df_optimization.append({"Time": node.attrib.get("time"), "Room": node.attrib.get("room"), "Distribution": node.attrib.get("distribution"), "Student": node.attrib.get("student")}, ignore_index = True)
    
    elif node.tag == "rooms":
        for room in node:
            roomid = room.attrib.get("id")
            cap = room.attrib.get("capacity")
            prevroomlist = []
            valuelist = []
            dayslist = []
            startlist = []
            lengthlist = []
            weekslist = []
            if len(list(child.tag for child in room.iter() if child is not room)) > 0:
                for child in room:
                    if child.tag == "travel":
                        prevroomid = child.attrib.get("room")
                        value = child.attrib.get("value")
                        prevroomlist.append(prevroomid)
                        valuelist.append(value)
                    elif child.tag == "unavailable":
                        days = child.attrib.get("days")
                        start = child.attrib.get("start")
                        length = child.attrib.get("length")
                        weeks = child.attrib.get("weeks")
                        dayslist.append(days)
                        startlist.append(start)
                        lengthlist.append(length)
                        weekslist.append(weeks)
            if len(prevroomlist) == 0:
                prevroomlist = None
            if len(valuelist) == 0:
                valuelist = None
            if len(dayslist) == 0:
                dayslist = None
            if len(startlist) == 0:
                startlist = None
            if len(lengthlist) == 0:
                lengthlist = None
            if len(weekslist) == 0:
                weekslist = None
            df_rooms = df_rooms.append(pd.Series([roomid, cap, prevroomlist, valuelist, dayslist, startlist, lengthlist, weekslist], index = columns_rooms), ignore_index = True)
            
    elif node.tag == "courses":
        for course in node:
            #print(course.tag)
            courseid = course.attrib.get("id")
            configlist = []
            for config in course:
                #print(config.tag)
                configid = config.attrib.get("id")
                configlist.append(configid)
                subpartlist = []
                for subpart in config:
                    #print(subpart.tag)
                    subpartid = subpart.attrib.get("id")
                    subpartlist.append(subpartid)
                    claselist = []
                    for clase in subpart:
                        #print(clase.tag)
                        claseid = clase.attrib.get("id")
                        claselist.append(claseid)
                        claselimit = clase.attrib.get("limit")
                        claseparent = clase.attrib.get("parent") if clase.attrib.get("parent") is not None else None
                        df_classes = df_classes.append(pd.Series([claseid, claselimit, claseparent], index = columns_classes), ignore_index = True)
                        if len(list(child.tag for child in clase.iter() if child is not clase)) > 0:
                            for child in clase:
                                #print(child.tag)
                                if child.tag == "room":
                                    roomid = child.attrib.get("id")
                                    roompenalty = child.attrib.get("penalty")
                                    df_relation_class_room = df_relation_class_room.append(pd.Series([claseid, roomid, roompenalty], index = columns_relation_class_room), ignore_index = True)
                                elif child.tag == "time":
                                    timedays = child.attrib.get("days")
                                    timestart = child.attrib.get("start")
                                    timelength = child.attrib.get("length")
                                    timeweeks = child.attrib.get("weeks")
                                    timepenalty = child.attrib.get("penalty")
                                    df_relation_class_time = df_relation_class_time.append(pd.Series([claseid, timedays, timestart, timelength, timeweeks, timepenalty], index = columns_relation_class_time), ignore_index = True)
                    df_subparts = df_subparts.append(pd.Series([subpartid, claselist], index = columns_subparts), ignore_index = True)
                df_configs = df_configs.append(pd.Series([configid, subpartlist], index = columns_configs), ignore_index = True)
            df_courses = df_courses.append(pd.Series([courseid, configlist], index = columns_courses), ignore_index = True)
                                    
    elif node.tag == "distributions":
        contador = 1
        for distribution in node:
            #print(distribution.tag)
            distribid = contador
            distribtype = distribution.attrib.get("type")
            distribrequired = distribution.attrib.get("required") if distribution.attrib.get("required") is not None else None
            distribpenalty = distribution.attrib.get("penalty") if distribution.attrib.get("penalty") is not None else None
            listaclases = []
            for clase in distribution:
                #print(clase.tag)
                listaclases.append(clase.attrib.get("id"))
            df_distributions = df_distributions.append(pd.Series([distribid, distribtype, distribrequired, distribpenalty, listaclases], index = columns_distributions), ignore_index = True)
            contador += 1
             
    elif node.tag == "students":
        for student in node:
            studentid = student.attrib.get("id")
            listacourses = []
            for course in student:
                listacourses.append(course.attrib.get("id"))
            df_students = df_students.append(pd.Series([studentid, listacourses], index = columns_students), ignore_index = True)
            
            


print("################################################################################################################")
print("DataFrame Problem")
display(df_problem)
print("################################################################################################################")
print("DataFrame Optimization")
display(df_optimization)
print("################################################################################################################")
print("DataFrame Rooms")
display(df_rooms)
print("################################################################################################################")
print("DataFrame Courses")
display(df_courses)
print("################################################################################################################")
print("DataFrame Configs")
display(df_configs)
print("################################################################################################################")
print("DataFrame Subparts")
display(df_subparts)
print("################################################################################################################")
print("DataFrame Classes")
display(df_classes)
print("################################################################################################################")
print("DataFrame Distributions")
display(df_distributions)
print("################################################################################################################")
print("DataFrame Students")
display(df_students)
print("################################################################################################################")
print("DataFrame RelationClassRoom")
display(df_relation_class_room)
print("################################################################################################################")
print("DataFrame RelationClassTime")
display(df_relation_class_time)
print("################################################################################################################")

################################################################################################################
DataFrame Problem


Name NrDays SlotsPerDay NrWeeks
0  muni-fi-spr16      7         288      15

################################################################################################################
DataFrame Optimization


Time Room Distribution Student
0    3    1           10       5

################################################################################################################
DataFrame Rooms


...

################################################################################################################
DataFrame RelationClassRoom


ClassId RoomId RoomPenalty
0          1     18           0
1         15     23           0
2         15      8           0
3         15     12           0
4         16     23           4
...      ...    ...         ...
2404     526     27           4
2405     526     30           0
2406     526      6           0
2407     526      7           1
2408     526     17           1

[2409 rows x 3 columns]

################################################################################################################
DataFrame RelationClassTime


ClassId TimeDays TimeStart TimeLength        TimeWeeks TimePenalty
0          1  0000100       168         46  011110111111110           0
1          2  1000000        96         46  011111011111110           0
2          2  0000100        96         46  011110111111110           0
3          2  1000000       108         46  011111011111110           0
4          2  0000100       108         46  011110111111110           0
...      ...      ...       ...        ...              ...         ...
9551     571  1000000       181         18  010101010101010           0
9552     572  1000000       200         18  011111011111110           0
9553     573  0001000        96         18  010101010101010           0
9554     574  0001000       115         18  011111111111110           0
9555     575  0010000       162         18  011111111111110           0

[9556 rows x 6 columns]

################################################################################################################


In [184]:
#Pasar a diccionarios las tablas de pandas 
dicc_cursos = {}
for index, row in df_courses.iterrows():
    dicc_cursos[int(row["CourseId"])] = [int(x) for x in row["ConfigIdList"]]   
    
dicc_configuraciones = {}
for index, row in df_configs.iterrows():
    dicc_configuraciones[int(row["ConfigId"])] = [int(x) for x in row["SubpartIdList"]]

dicc_subpartes = {}
for index, row in df_subparts.iterrows():
    dicc_subpartes[int(row["SubpartId"])] = [int(x) for x in row["ClassIdList"]]

dicc_clases = {}
for index, row in df_classes.iterrows():
    dicc_clases[int(row["ClassId"])] = [int(x) for x in row["ClassLimit"]]

In [185]:
#CONJUNTOS

In [186]:
#Asignaciones de cursos hechas a mano porque tienen más de una configuración
cursos_sin_asignar = {}
configuraciones_sin_asignar = {}
subpartes_sin_asignar = {}

#Conjunto de cursos
cursos = {}
for curso in dicc_cursos:
    if len(dicc_cursos[curso]) == 1:
        cursos[curso] = curso
    else:
        cursos_sin_asignar[curso] = dicc_cursos[curso]

#Conjunto de configuraciones
configuraciones = {}
for configuracion in dicc_configuraciones:
    for configs in cursos_sin_asignar.values():
        if configuracion not in configs:
            configuraciones[configuracion] = configuracion
        else:
            configuraciones_sin_asignar[configuracion] = dicc_configuraciones[configuracion]

#Conjunto de Subpartes
subpartes = {}
for subparte in dicc_subpartes:
    for subparts in configuraciones_sin_asignar.values():
        if subparte not in subparts:
            subpartes[subparte] = subparte
        else:
            subpartes_sin_asignar[subparte] = dicc_subpartes[subparte]

#Conjunto Clases
clases = {}
for clase in dicc_clases:
    for classes in subpartes_sin_asignar.values():
        if clase not in classes:
            clases[clase] = clase

#D distribuciones
distribuciones = {}
for index, row in df_distributions.iterrows():
    if row["DistributionType"] == "SameAttendees" or row["DistributionType"] == "SameTime" or row["DistributionType"] == "SameRoom" or row["DistributionType"] == "SameDays" or row["DistributionType"] == "Precedence" or row["DistributionType"] == "NotOverlap" or row["DistributionType"] == "SameWeeks":
        distribuciones[row["DistributionId"]] = row["DistributionId"]


In [187]:
#SUBCONJUNTOS

In [241]:
#Tc = periodos disponibles para la clase c, donde t=(Wt, Dt, ht, lent) 
dicc_Tc = {}
dicc_tiempos = {}
tiempos = {}
for index,row in df_relation_class_time.iterrows():
    if int(row["ClassId"]) not in dicc_Tc.keys():
        dicc_Tc[int(row["ClassId"])] = []
    dicc_Tc[int(row["ClassId"])].append(index)
    dicc_tiempos[index] = [row["TimeWeeks"], row["TimeDays"], int(row["TimeStart"]), int(row["TimeLength"])]
    tiempos[index] = index
#print(dicc_tiempos)
print(dicc_Tc)
#print(tiempos)

{1: [0], 2: [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18], 3: [19], 4: [20], 5: [21], 6: [22], 7: [23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48], 8: [49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76], 9: [77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104], 10: [105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148], 11: [149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192], 12: [193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 20

In [189]:
#Sc = salas disponibles para la clase c
dicc_Sc = {}
for index, row in df_relation_class_room.iterrows():
    if int(row["ClassId"]) not in dicc_Sc.keys():
        dicc_Sc[int(row["ClassId"])] = []
    dicc_Sc[int(row["ClassId"])].append(int(row["RoomId"]))

for i in range(1,len(clases)+1):
    if i not in dicc_Sc.keys():
        dicc_Sc[i] = []
#print(sorted(dicc_Sc))

In [190]:
#Fk = configuraciones del curso k
dicc_Fk = {}
for curso in dicc_cursos:
    if len(dicc_cursos[curso]) == 1:
        dicc_Fk[curso] = dicc_cursos[curso]
#print(dicc_Fk)

In [191]:
#Pf = subpartes de la configuracion f
dicc_Pf = {}
for configuracion in dicc_configuraciones:
    dicc_Pf[configuracion] = dicc_configuraciones[configuracion]
#print(dicc_Pf)

In [192]:
#Cp = clases de la subparte p
dicc_Cp = {}
for subparte in dicc_subpartes:
    dicc_Cp[subparte] = dicc_subpartes[subparte]
#print(dicc_Cp)

In [193]:
#UTs = periodo no disponible para la sala s
dicc_UTs = {}
for index, col in df_rooms.iterrows():
    if col["UnavailableDaysList"] != None:
        sem_no_disp = col["UnavailableWeeksList"]
        dias_no_disp = col["UnavailableDaysList"]
        hor_no_disp = [int(x) for x in col["UnavailableStartList"]]
        largo_no_disp = [int(x) for x in col["UnavailableLengthList"]]
        dicc_UTs[int(col["RoomId"])] = [sem_no_disp, dias_no_disp, hor_no_disp, largo_no_disp]
    else:
        dicc_UTs[int(col["RoomId"])] = [] 
#print(dicc_UTs)

In [194]:
#SUBCONJUNTOS DE DISTRIBUCIONES

In [195]:
## D1 = distribuciones de tipo 1 (SameAttendees) lista con id's
#distribución SameAttendees dura
D1 =[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameAttendees" and row["DistributionRequired"]=="true":
        D1.append(int(row["DistributionId"]))
#print(D1)

#distribución SameAttendees blanda
D1_B =[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameAttendees" and row["DistributionRequired"]==None:
        D1_B.append(int(row["DistributionId"]))
#print(D1_B)

In [196]:
## D2 = distribuciones de tipo 2 (SameStart) lista con id's
#distribución SameStart dura
D2 =[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameStart" and row["DistributionRequired"]=="true":
        D2.append(int(row["DistributionId"]))
#print(D2)

#distribución SameStart blanda
D2_B =[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameStart" and row["DistributionRequired"]==None:
        D2_B.append(int(row["DistributionId"]))
#print(D2_B)

In [197]:
## D3 = D3=distribuciones de tipo 3 (SameRoom) lista con id's
#distribución SameRoom dura
D3=[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameRoom" and row["DistributionRequired"]=="true":
        D3.append(int(row["DistributionId"]))
#print(D3)

#distribución SameRoom blanda
D3_B =[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameRoom" and row["DistributionRequired"]==None:
        D3_B.append(int(row["DistributionId"]))
#print(D3_B)

In [198]:
## D4 = distribuciones de tipo 4 (SameTime) lista con id's
#distribución SameTime dura
D4=[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameTime" and row["DistributionRequired"]=="true":
        D4.append(int(row["DistributionId"]))
#print(D4)

#distribución SameTime blanda
D4_B =[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameTime" and row["DistributionRequired"]==None:
        D4_B.append(int(row["DistributionId"]))
#print(D4_B)

In [238]:
## D5 = distribuciones de tipo 5 (SameDays) lista con id's
#distribución SameDays dura
D5=[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameDays" and row["DistributionRequired"]=="true":
        D5.append(int(row["DistributionId"]))
#print(D5)

#distribución SameDays blanda
D5_B =[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameDays" and row["DistributionRequired"]==None:
        D5_B.append(int(row["DistributionId"]))
#print(D5_B)

In [200]:
## D6 = distribuciones de tipo 6 (SameWeeks) lista con id's
#distribución SameWeeks dura
D6=[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameWeeks" and row["DistributionRequired"]=="true":
        D6.append(int(row["DistributionId"]))
#print(D6)

#distribución SameWeeks blanda
D6_B =[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameWeeks" and row["DistributionRequired"]==None:
        D6_B.append(int(row["DistributionId"]))
#print(D6_B)

In [201]:
## D7 = distribuciones de tipo 7 (Precendence) lista con id's
#distribución Precendence dura
D7=[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="Precedence" and row["DistributionRequired"]=="true":
        D7.append(int(row["DistributionId"]))
#print(D7)

#distribución Precendence blanda
D7_B =[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="Precedence" and row["DistributionRequired"]==None:
        D7_B.append(int(row["DistributionId"]))
#print(D7_B)

In [202]:
## D8 = distribuciones de tipo 8 (NotOverlap) lista con id's
#distribución NotOverlap dura
D8=[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="NotOverlap" and row["DistributionRequired"]=="true":
        D8.append(int(row["DistributionId"]))
#print(D8)

#distribución NotOverlap blanda
D8_B =[]
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="NotOverlap" and row["DistributionRequired"]==None:
        D8_B.append(int(row["DistributionId"]))
#print(D8_B)

In [203]:
#SAi=clases de la distribución SameAttendees i (dura)
Sa = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameAttendees" and row["DistributionRequired"]=="true":
        Sa[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            Sa[int(row["DistributionId"])].append(int(i))
#print(Sa)

#SABi=clases de la distribución SameAttendees i (blanda)
SaB = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameAttendees" and row["DistributionRequired"]==None:
        SaB[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            SaB[int(row["DistributionId"])].append(int(i))
#print(SaB)

In [204]:
#SSi =clases de la distribución SameStart i (dura)
SS = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameStart" and row["DistributionRequired"]=="true":
        SS[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            SS[int(row["DistributionId"])].append(int(i))


#SSBi=clases de la distribución SameStart i  (blanda)
SSB = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameStart" and row["DistributionRequired"]==None:
        SSB[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            SSB[int(row["DistributionId"])].append(int(i))
#print(SSB)

In [205]:
#DUPLICADO ANTERIOR Y MODIFICADO
#SSi =clases de la distribución SameStart i (dura)
SS = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameStart" and row["DistributionRequired"]=="true":
        SS[int(row["ClassesList"][0])] = [int(x) for x in row["ClassesList"]]

for i in range(1,len(dicc_tiempos)+1):
    if i not in SS.keys():
        SS[i] = []
#SSBi=clases de la distribución SameStart i  (blanda)
SSB = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameStart" and row["DistributionRequired"]==None:
        SSB[int(row["ClassesList"][0])] = [int(x) for x in row["ClassesList"]]

for i in range(1,len(dicc_tiempos)+1):
    if i not in SSB.keys():
        SSB[i] = []

In [206]:
#SRi =clases de la distribución SameRoom i (dura) (dura)
SR = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameRoom" and row["DistributionRequired"]=="true":
        SR[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            SR[int(row["DistributionId"])].append(int(i))
#print(SR)

#SRBi =clases de la distribución SameRoom i (blanda)
SRB = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameRoom" and row["DistributionRequired"]==None:
        SRB[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            SRB[int(row["DistributionId"])].append(int(i))
#print(SRB)

In [207]:
#DUPLICADO ANTERIOR Y MODIFICADO
#SRi =clases de la distribución SameRoom i (dura) (dura)
SR = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameRoom" and row["DistributionRequired"]=="true":
        SR[int(row["ClassesList"][0])] = [int(x) for x in row["ClassesList"]]
        
for i in range(1,len(dicc_tiempos)+1):
    if i not in SR.keys():
        SR[i] = []
print(SR)

#SRBi =clases de la distribución SameRoom i (blanda)
SRB = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameRoom" and row["DistributionRequired"]==None:
        SRB[int(row["ClassesList"][0])] = [int(x) for x in row["ClassesList"]]
for i in range(1,len(dicc_tiempos)+1):
    if i not in SRB.keys():
        SRB[i] = []
print(SRB)

{318: [318, 319], 320: [320, 321], 112: [112, 113], 114: [114, 115], 116: [116, 117], 118: [118, 119], 120: [120, 121], 472: [472, 471], 289: [289, 290], 291: [291, 292], 340: [340, 341], 342: [342, 343], 344: [344, 345], 346: [346, 347], 348: [348, 349], 350: [350, 351], 459: [459, 460], 461: [461, 462], 477: [477, 478], 479: [479, 480], 481: [481, 482], 84: [84, 85], 237: [237, 238], 247: [247, 248], 359: [359, 360], 1: [], 2: [], 3: [], 4: [], 5: [], 6: [], 7: [], 8: [], 9: [], 10: [], 11: [], 12: [], 13: [], 14: [], 15: [], 16: [], 17: [], 18: [], 19: [], 20: [], 21: [], 22: [], 23: [], 24: [], 25: [], 26: [], 27: [], 28: [], 29: [], 30: [], 31: [], 32: [], 33: [], 34: [], 35: [], 36: [], 37: [], 38: [], 39: [], 40: [], 41: [], 42: [], 43: [], 44: [], 45: [], 46: [], 47: [], 48: [], 49: [], 50: [], 51: [], 52: [], 53: [], 54: [], 55: [], 56: [], 57: [], 58: [], 59: [], 60: [], 61: [], 62: [], 63: [], 64: [], 65: [], 66: [], 67: [], 68: [], 69: [], 70: [], 71: [], 72: [], 73: [], 74

In [208]:
#STi=clases de la distribución SameTime i (dura)
ST = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameTime" and row["DistributionRequired"]=="true":
        ST[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            ST[int(row["DistributionId"])].append(int(i))
#print(ST)

#STi=clases de la distribución SameTime i  (blanda)
STB = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameTime" and row["DistributionRequired"]==None:
        STB[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            STB[int(row["DistributionId"])].append(int(i))
#print(STB)

In [209]:
#DUPLICADO ANTERIOR Y MODIFICADO
#STi=clases de la distribución SameTime i (dura)
ST = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameTime" and row["DistributionRequired"]=="true":
        ST[int(row["ClassesList"][0])] = [int(x) for x in row["ClassesList"]]
        
for i in range(1,len(dicc_tiempos)+1):
    if i not in ST.keys():
        ST[i] = []
print(ST)
#STi=clases de la distribución SameTime i  (blanda)
STB = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameTime" and row["DistributionRequired"]==None:
        STB[int(row["ClassesList"][0])] = [int(x) for x in row["ClassesList"]]
        
for i in range(1,len(dicc_tiempos)+1):
    if i not in STB.keys():
        STB[i] = []
print(STB)

{340: [340, 341], 342: [342, 343], 344: [344, 345], 346: [346, 347], 348: [348, 349], 350: [350, 351], 459: [459, 460], 461: [461, 462], 477: [477, 478], 479: [479, 480], 481: [481, 482], 84: [84, 85], 237: [237, 238], 247: [247, 248], 18: [18, 391], 17: [17, 374], 20: [20, 465], 10: [10, 318], 11: [11, 319], 12: [12, 320], 13: [13, 321], 14: [14, 322], 7: [7, 211], 250: [250, 251], 252: [252, 253], 254: [254, 255], 256: [256, 257], 8: [8, 220], 9: [9, 221], 2: [2, 31], 1: [], 3: [], 4: [], 5: [], 6: [], 15: [], 16: [], 19: [], 21: [], 22: [], 23: [], 24: [], 25: [], 26: [], 27: [], 28: [], 29: [], 30: [], 31: [], 32: [], 33: [], 34: [], 35: [], 36: [], 37: [], 38: [], 39: [], 40: [], 41: [], 42: [], 43: [], 44: [], 45: [], 46: [], 47: [], 48: [], 49: [], 50: [], 51: [], 52: [], 53: [], 54: [], 55: [], 56: [], 57: [], 58: [], 59: [], 60: [], 61: [], 62: [], 63: [], 64: [], 65: [], 66: [], 67: [], 68: [], 69: [], 70: [], 71: [], 72: [], 73: [], 74: [], 75: [], 76: [], 77: [], 78: [], 79

In [239]:
#SDi=clases de la distribución SameDays i (dura)
SD = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameDays" and row["DistributionRequired"]=="true":
        SD[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            SD[int(row["DistributionId"])].append(int(i))
print(SD)

#SDBi=clases de la distribución SameDays i (blanda)
SDB = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameDays" and row["DistributionRequired"]==None:
        SDB[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            SDB[int(row["DistributionId"])].append(int(i))
#print(SDB)


{162: [318, 319], 165: [320, 321], 168: [112, 113], 171: [114, 115], 174: [116, 117], 177: [118, 119], 180: [120, 121], 183: [472, 471], 186: [289, 290], 189: [291, 292], 195: [218, 219], 198: [243, 244], 201: [294, 295], 204: [296, 297], 207: [298, 299], 210: [300, 301], 213: [302, 303], 216: [335, 336], 219: [359, 360], 222: [421, 422, 423], 225: [463, 464], 231: [516, 517], 233: [328, 326], 239: [390, 526], 348: [216, 249], 353: [103, 104], 359: [340, 341], 362: [342, 343], 365: [344, 345], 368: [346, 347], 371: [348, 349], 374: [350, 351], 377: [459, 460], 380: [461, 462], 383: [477, 478], 386: [479, 480], 389: [481, 482], 392: [84, 85], 395: [237, 238], 398: [247, 248], 401: [18, 391], 403: [17, 374], 405: [20, 465], 407: [10, 318], 409: [11, 319], 411: [12, 320], 413: [13, 321], 415: [14, 322], 417: [7, 211], 419: [250, 251], 421: [252, 253], 423: [254, 255], 425: [256, 257], 427: [8, 220], 429: [9, 221], 431: [2, 31], 436: [155, 156], 439: [153, 154], 442: [93, 94]}


In [240]:
#DUPLICADO ANTERIOR Y MODIFICADO
#SDi=clases de la distribución SameDays i (dura)
SD = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameDays" and row["DistributionRequired"]=="true":
        SD[int(row["ClassesList"][0])] = [int(x) for x in row["ClassesList"]]
for i in range(1,len(dicc_tiempos)+1):
    if i not in SD.keys():
        SD[i] = []
print(SD)

#SDBi=clases de la distribución SameDays i (blanda)
SDB = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameDays" and row["DistributionRequired"]==None:
        SDB[int(row["ClassesList"][0])] = [int(x) for x in row["ClassesList"]]
for i in range(1,len(dicc_tiempos)+1):
    if i not in SDB.keys():
        SDB[i] = []
#print(SDB)


{318: [318, 319], 320: [320, 321], 112: [112, 113], 114: [114, 115], 116: [116, 117], 118: [118, 119], 120: [120, 121], 472: [472, 471], 289: [289, 290], 291: [291, 292], 218: [218, 219], 243: [243, 244], 294: [294, 295], 296: [296, 297], 298: [298, 299], 300: [300, 301], 302: [302, 303], 335: [335, 336], 359: [359, 360], 421: [421, 422, 423], 463: [463, 464], 516: [516, 517], 328: [328, 326], 390: [390, 526], 216: [216, 249], 103: [103, 104], 340: [340, 341], 342: [342, 343], 344: [344, 345], 346: [346, 347], 348: [348, 349], 350: [350, 351], 459: [459, 460], 461: [461, 462], 477: [477, 478], 479: [479, 480], 481: [481, 482], 84: [84, 85], 237: [237, 238], 247: [247, 248], 18: [18, 391], 17: [17, 374], 20: [20, 465], 10: [10, 318], 11: [11, 319], 12: [12, 320], 13: [13, 321], 14: [14, 322], 7: [7, 211], 250: [250, 251], 252: [252, 253], 254: [254, 255], 256: [256, 257], 8: [8, 220], 9: [9, 221], 2: [2, 31], 155: [155, 156], 153: [153, 154], 93: [93, 94], 1: [], 3: [], 4: [], 5: [], 6:

In [212]:
#PRi=clases de la distribución Precedence i (dura)
PR = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="Precedence" and row["DistributionRequired"]=="true":
        PR[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            PR[int(row["DistributionId"])].append(int(i))
#print(PR)

#PRBi=clases de la distribución Precedence i (blanda)
PRB = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="Precedence" and row["DistributionRequired"]==None:
        PRB[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            PRB[int(row["DistributionId"])].append(int(i))
#print(PRB)

In [213]:
#NOi=clases de la distribución NotOverlap i (dura)
NO = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="NotOverlap" and row["DistributionRequired"]=="true":
        NO[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            NO[int(row["DistributionId"])].append(int(i))
#print(NO)

#NOBi=clases de la distribución NotOverlap i (blanda)
NOB = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="NotOverlap" and row["DistributionRequired"]==None:
        NOB[int(row["DistributionId"])] = []
        for i in row["ClassesList"]:
            NOB[int(row["DistributionId"])].append(int(i))
#print(NOB)

In [214]:
#PARÁMETROS

In [215]:
dicc_T = {}
for index,row in df_relation_class_time.iterrows():
    if int(row["ClassId"]) not in dicc_T.keys():
        dicc_T[int(row["ClassId"])] = []
    dicc_T[int(row["ClassId"])].append([row["TimeWeeks"], row["TimeDays"], int(row["TimeStart"]), int(row["TimeLength"])])
print(dicc_Tc)



{1: [0], 2: [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18], 3: [19], 4: [20], 5: [21], 6: [22], 7: [23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48], 8: [49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76], 9: [77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104], 10: [105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148], 11: [149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192], 12: [193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 20

In [243]:
#t[semanas]=semanas correspondientes al periodo t de la clase cWt
dicc_Wt = {}
for tiempo in dicc_tiempos:
    if tiempo not in dicc_Wt.keys():
        dicc_Wt[tiempo] = []
    dicc_Wt[tiempo].append(dicc_tiempos[tiempo][0])
#print(dicc_Wc)
print(dicc_tiempos)

{0: ['011110111111110', '0000100', 168, 46], 1: ['011111011111110', '1000000', 96, 46], 2: ['011110111111110', '0000100', 96, 46], 3: ['011111011111110', '1000000', 108, 46], 4: ['011110111111110', '0000100', 108, 46], 5: ['011111011111110', '1000000', 120, 46], 6: ['011110111111110', '0000100', 120, 46], 7: ['011111011111110', '1000000', 132, 46], 8: ['011110111111110', '0000100', 132, 46], 9: ['011111011111110', '1000000', 144, 46], 10: ['011110111111110', '0000100', 144, 46], 11: ['011111011111110', '1000000', 156, 46], 12: ['011110111111110', '0000100', 156, 46], 13: ['011111011111110', '1000000', 168, 46], 14: ['011110111111110', '0000100', 168, 46], 15: ['011111011111110', '1000000', 180, 46], 16: ['011110111111110', '0000100', 180, 46], 17: ['011111011111110', '1000000', 192, 46], 18: ['011110111111110', '0000100', 192, 46], 19: ['011111111111110', '0100000', 168, 22], 20: ['011111011111110', '1000000', 144, 46], 21: ['010101010101010', '1000000', 196, 39], 22: ['001010101010100

In [232]:
#t[dias]=días correspondientes al periodo t Dt
dicc_Dt = {}
for tiempo in dicc_tiempos:
    if tiempo not in dicc_Dt.keys():
        dicc_Dt[tiempo] = []
    dicc_Dt[tiempo].append(dicc_tiempos[tiempo][1])
print(dicc_Dc)

{0: ['0000100'], 1: ['1000000'], 2: ['0000100'], 3: ['1000000'], 4: ['0000100'], 5: ['1000000'], 6: ['0000100'], 7: ['1000000'], 8: ['0000100'], 9: ['1000000'], 10: ['0000100'], 11: ['1000000'], 12: ['0000100'], 13: ['1000000'], 14: ['0000100'], 15: ['1000000'], 16: ['0000100'], 17: ['1000000'], 18: ['0000100'], 19: ['0100000'], 20: ['1000000'], 21: ['1000000'], 22: ['0010000'], 23: ['1000000'], 24: ['0100000'], 25: ['0010000'], 26: ['0001000'], 27: ['0000100'], 28: ['1000000'], 29: ['0100000'], 30: ['0010000'], 31: ['0001000'], 32: ['0000100'], 33: ['1000000'], 34: ['0100000'], 35: ['0010000'], 36: ['0001000'], 37: ['0000100'], 38: ['1000000'], 39: ['0100000'], 40: ['0010000'], 41: ['0001000'], 42: ['0000100'], 43: ['0100000'], 44: ['0010000'], 45: ['0000100'], 46: ['0100000'], 47: ['0010000'], 48: ['0000100'], 49: ['1000000'], 50: ['0100000'], 51: ['0010000'], 52: ['0001000'], 53: ['0000100'], 54: ['1000000'], 55: ['0100000'], 56: ['0010000'], 57: ['0001000'], 58: ['0000100'], 59: ['

In [218]:
#t[slot}=slot en el que inicia el periodo t Ht
dicc_Ht = {}
for tiempo in dicc_tiempos:
    if tiempo not in dicc_Ht.keys():
        dicc_Ht[tiempo] = []
    dicc_Ht[tiempo].append(dicc_tiempos[tiempo][2])
#print(dicc_Hc)

In [219]:
#t[len]=duración del periodo t Lh
dicc_Lt = {}
for tiempo in dicc_tiempos:
    if tiempo not in dicc_Lt.keys():
        dicc_Lt[tiempo] = []
    dicc_Lt[tiempo].append(dicc_tiempos[tiempo][3])
#print(dicc_Lc)

In [220]:
#PTc,t=penalización asociada a asignar la clase c en el tiempo t
dicc_PTct = {}
for index, row in df_relation_class_time.iterrows():
    llave = (int(row["ClassId"]),int(index))
    dicc_PTct[llave] = int(row["TimePenalty"]) 
#print(dicc_PTct)

In [221]:
#PSc,s=penalización asociada a asignar la clase c en la sala s
dicc_PScs = {}
for index, row in df_relation_class_room.iterrows():
    llave = (int(row["ClassId"]),int(row["RoomId"]))
    dicc_PScs[llave] = int(row["RoomPenalty"]) 
#print(dicc_PScs)

In [222]:
#PD1,i=penalización asociada a la distribución i de tipo 1 (SamAttendees)
dicc_PD1i = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"] == "SameAttendees":
        if row["DistributionPenalty"] is None:
            dp = 0
        else:
            dp = int(row["DistributionPenalty"])
        dicc_PD1i[int(row["DistributionId"])] = dp

#PD2,i=penalización asociada a la distribución i de tipo 2 (SameStart)
dicc_PD2i = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"] == "SameStart":
        if row["DistributionPenalty"] is None:
            dp = 0
        else:
            dp = int(row["DistributionPenalty"])
        dicc_PD2i[int(row["DistributionId"])] = dp
        
#PD3,i=penalización asociada a la distribución i de tipo 3 (SameRoom)
dicc_PD3i = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"] == "SameRoom":
        if row["DistributionPenalty"] is None:
            dp = 0
        else:
            dp = int(row["DistributionPenalty"])
        dicc_PD3i[int(row["DistributionId"])] = dp
        
#PD4,i=penalización asociada a la distribución i de tipo 4(SameTime)       
dicc_PD4i = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"] == "SameTime":
        if row["DistributionPenalty"] is None:
            dp = 0
        else:
            dp = int(row["DistributionPenalty"])
        dicc_PD4i[int(row["DistributionId"])] = dp

#PD5,i=penalización asociada a la distribución i de tipo 5 (SameDays) 
dicc_PD5i = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"] == "SameDays":
        if row["DistributionPenalty"] is None:
            dp = 0
        else:
            dp = int(row["DistributionPenalty"])
        dicc_PD5i[int(row["DistributionId"])] = dp
        
#PD6,i=penalización asociada a la distribución i de tipo 6 (SameWeeks)
dicc_PD6i = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"] == "SameWeeks":
        if row["DistributionPenalty"] is None:
            dp = 0
        else:
            dp = int(row["DistributionPenalty"])
        dicc_PD6i[int(row["DistributionId"])] = dp
        
#PD7,i=penalización asociada a la distribución i de tipo 7(Precedence) 
dicc_PD7i = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"] == "Precedence":
        if row["DistributionPenalty"] is None:
            dp = 0
        else:
            dp = int(row["DistributionPenalty"])
        dicc_PD7i[int(row["DistributionId"])] = dp
        
#PD8,i=penalización asociada a la distribución i de tipo 8(NotOverlap) 
dicc_PD8i = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"] == "NotOverlap":
        if row["DistributionPenalty"] is None:
            dp = 0
        else:
            dp = int(row["DistributionPenalty"])
        dicc_PD8i[int(row["DistributionId"])] = dp

In [223]:
#GUROBI

In [224]:
from gurobipy import *
from random   import *
import numpy as np
import gurobipy as gp
from gurobipy import GRB

In [231]:
for c in clases:
    for t in tiempos:
        print(c,t)

1 0
1 1
1 2
1 3
1 4
1 5
1 6
1 7
1 8
1 9
1 10
1 11
1 12
1 13
1 14
1 15
1 16
1 17
1 18
1 19
1 20
1 21
1 22
1 23
1 24
1 25
1 26
1 27
1 28
1 29
1 30
1 31
1 32
1 33
1 34
1 35
1 36
1 37
1 38
1 39
1 40
1 41
1 42
1 43
1 44
1 45
1 46
1 47
1 48
1 49
1 50
1 51
1 52
1 53
1 54
1 55
1 56
1 57
1 58
1 59
1 60
1 61
1 62
1 63
1 64
1 65
1 66
1 67
1 68
1 69
1 70
1 71
1 72
1 73
1 74
1 75
1 76
1 77
1 78
1 79
1 80
1 81
1 82
1 83
1 84
1 85
1 86
1 87
1 88
1 89
1 90
1 91
1 92
1 93
1 94
1 95
1 96
1 97
1 98
1 99
1 100
1 101
1 102
1 103
1 104
1 105
1 106
1 107
1 108
1 109
1 110
1 111
1 112
1 113
1 114
1 115
1 116
1 117
1 118
1 119
1 120
1 121
1 122
1 123
1 124
1 125
1 126
1 127
1 128
1 129
1 130
1 131
1 132
1 133
1 134
1 135
1 136
1 137
1 138
1 139
1 140
1 141
1 142
1 143
1 144
1 145
1 146
1 147
1 148
1 149
1 150
1 151
1 152
1 153
1 154
1 155
1 156
1 157
1 158
1 159
1 160
1 161
1 162
1 163
1 164
1 165
1 166
1 167
1 168
1 169
1 170
1 171
1 172
1 173
1 174
1 175
1 176
1 177
1 178
1 179
1 180
1 181
1 182
1 183
1 184


1 1865
1 1866
1 1867
1 1868
1 1869
1 1870
1 1871
1 1872
1 1873
1 1874
1 1875
1 1876
1 1877
1 1878
1 1879
1 1880
1 1881
1 1882
1 1883
1 1884
1 1885
1 1886
1 1887
1 1888
1 1889
1 1890
1 1891
1 1892
1 1893
1 1894
1 1895
1 1896
1 1897
1 1898
1 1899
1 1900
1 1901
1 1902
1 1903
1 1904
1 1905
1 1906
1 1907
1 1908
1 1909
1 1910
1 1911
1 1912
1 1913
1 1914
1 1915
1 1916
1 1917
1 1918
1 1919
1 1920
1 1921
1 1922
1 1923
1 1924
1 1925
1 1926
1 1927
1 1928
1 1929
1 1930
1 1931
1 1932
1 1933
1 1934
1 1935
1 1936
1 1937
1 1938
1 1939
1 1940
1 1941
1 1942
1 1943
1 1944
1 1945
1 1946
1 1947
1 1948
1 1949
1 1950
1 1951
1 1952
1 1953
1 1954
1 1955
1 1956
1 1957
1 1958
1 1959
1 1960
1 1961
1 1962
1 1963
1 1964
1 1965
1 1966
1 1967
1 1968
1 1969
1 1970
1 1971
1 1972
1 1973
1 1974
1 1975
1 1976
1 1977
1 1978
1 1979
1 1980
1 1981
1 1982
1 1983
1 1984
1 1985
1 1986
1 1987
1 1988
1 1989
1 1990
1 1991
1 1992
1 1993
1 1994
1 1995
1 1996
1 1997
1 1998
1 1999
1 2000
1 2001
1 2002
1 2003
1 2004
1 2005
1 2006
1 2007

1 3588
1 3589
1 3590
1 3591
1 3592
1 3593
1 3594
1 3595
1 3596
1 3597
1 3598
1 3599
1 3600
1 3601
1 3602
1 3603
1 3604
1 3605
1 3606
1 3607
1 3608
1 3609
1 3610
1 3611
1 3612
1 3613
1 3614
1 3615
1 3616
1 3617
1 3618
1 3619
1 3620
1 3621
1 3622
1 3623
1 3624
1 3625
1 3626
1 3627
1 3628
1 3629
1 3630
1 3631
1 3632
1 3633
1 3634
1 3635
1 3636
1 3637
1 3638
1 3639
1 3640
1 3641
1 3642
1 3643
1 3644
1 3645
1 3646
1 3647
1 3648
1 3649
1 3650
1 3651
1 3652
1 3653
1 3654
1 3655
1 3656
1 3657
1 3658
1 3659
1 3660
1 3661
1 3662
1 3663
1 3664
1 3665
1 3666
1 3667
1 3668
1 3669
1 3670
1 3671
1 3672
1 3673
1 3674
1 3675
1 3676
1 3677
1 3678
1 3679
1 3680
1 3681
1 3682
1 3683
1 3684
1 3685
1 3686
1 3687
1 3688
1 3689
1 3690
1 3691
1 3692
1 3693
1 3694
1 3695
1 3696
1 3697
1 3698
1 3699
1 3700
1 3701
1 3702
1 3703
1 3704
1 3705
1 3706
1 3707
1 3708
1 3709
1 3710
1 3711
1 3712
1 3713
1 3714
1 3715
1 3716
1 3717
1 3718
1 3719
1 3720
1 3721
1 3722
1 3723
1 3724
1 3725
1 3726
1 3727
1 3728
1 3729
1 3730

1 5341
1 5342
1 5343
1 5344
1 5345
1 5346
1 5347
1 5348
1 5349
1 5350
1 5351
1 5352
1 5353
1 5354
1 5355
1 5356
1 5357
1 5358
1 5359
1 5360
1 5361
1 5362
1 5363
1 5364
1 5365
1 5366
1 5367
1 5368
1 5369
1 5370
1 5371
1 5372
1 5373
1 5374
1 5375
1 5376
1 5377
1 5378
1 5379
1 5380
1 5381
1 5382
1 5383
1 5384
1 5385
1 5386
1 5387
1 5388
1 5389
1 5390
1 5391
1 5392
1 5393
1 5394
1 5395
1 5396
1 5397
1 5398
1 5399
1 5400
1 5401
1 5402
1 5403
1 5404
1 5405
1 5406
1 5407
1 5408
1 5409
1 5410
1 5411
1 5412
1 5413
1 5414
1 5415
1 5416
1 5417
1 5418
1 5419
1 5420
1 5421
1 5422
1 5423
1 5424
1 5425
1 5426
1 5427
1 5428
1 5429
1 5430
1 5431
1 5432
1 5433
1 5434
1 5435
1 5436
1 5437
1 5438
1 5439
1 5440
1 5441
1 5442
1 5443
1 5444
1 5445
1 5446
1 5447
1 5448
1 5449
1 5450
1 5451
1 5452
1 5453
1 5454
1 5455
1 5456
1 5457
1 5458
1 5459
1 5460
1 5461
1 5462
1 5463
1 5464
1 5465
1 5466
1 5467
1 5468
1 5469
1 5470
1 5471
1 5472
1 5473
1 5474
1 5475
1 5476
1 5477
1 5478
1 5479
1 5480
1 5481
1 5482
1 5483

1 7080
1 7081
1 7082
1 7083
1 7084
1 7085
1 7086
1 7087
1 7088
1 7089
1 7090
1 7091
1 7092
1 7093
1 7094
1 7095
1 7096
1 7097
1 7098
1 7099
1 7100
1 7101
1 7102
1 7103
1 7104
1 7105
1 7106
1 7107
1 7108
1 7109
1 7110
1 7111
1 7112
1 7113
1 7114
1 7115
1 7116
1 7117
1 7118
1 7119
1 7120
1 7121
1 7122
1 7123
1 7124
1 7125
1 7126
1 7127
1 7128
1 7129
1 7130
1 7131
1 7132
1 7133
1 7134
1 7135
1 7136
1 7137
1 7138
1 7139
1 7140
1 7141
1 7142
1 7143
1 7144
1 7145
1 7146
1 7147
1 7148
1 7149
1 7150
1 7151
1 7152
1 7153
1 7154
1 7155
1 7156
1 7157
1 7158
1 7159
1 7160
1 7161
1 7162
1 7163
1 7164
1 7165
1 7166
1 7167
1 7168
1 7169
1 7170
1 7171
1 7172
1 7173
1 7174
1 7175
1 7176
1 7177
1 7178
1 7179
1 7180
1 7181
1 7182
1 7183
1 7184
1 7185
1 7186
1 7187
1 7188
1 7189
1 7190
1 7191
1 7192
1 7193
1 7194
1 7195
1 7196
1 7197
1 7198
1 7199
1 7200
1 7201
1 7202
1 7203
1 7204
1 7205
1 7206
1 7207
1 7208
1 7209
1 7210
1 7211
1 7212
1 7213
1 7214
1 7215
1 7216
1 7217
1 7218
1 7219
1 7220
1 7221
1 7222

...

42 7563
42 7564
42 7565
42 7566
42 7567
42 7568
42 7569
42 7570
42 7571
42 7572
42 7573
42 7574
42 7575
42 7576
42 7577
42 7578
42 7579
42 7580
42 7581
42 7582
42 7583
42 7584
42 7585
42 7586
42 7587
42 7588
42 7589
42 7590
42 7591
42 7592
42 7593
42 7594
42 7595
42 7596
42 7597
42 7598
42 7599
42 7600
42 7601
42 7602
42 7603
42 7604
42 7605
42 7606
42 7607
42 7608
42 7609
42 7610
42 7611
42 7612
42 7613
42 7614
42 7615
42 7616
42 7617
42 7618
42 7619
42 7620
42 7621
42 7622
42 7623
42 7624
42 7625
42 7626
42 7627
42 7628
42 7629
42 7630
42 7631
42 7632
42 7633
42 7634
42 7635
42 7636
42 7637
42 7638
42 7639
42 7640
42 7641
42 7642
42 7643
42 7644
42 7645
42 7646
42 7647
42 7648
42 7649
42 7650
42 7651
42 7652
42 7653
42 7654
42 7655
42 7656
42 7657
42 7658
42 7659
42 7660
42 7661
42 7662
42 7663
42 7664
42 7665
42 7666
42 7667
42 7668
42 7669
42 7670
42 7671
42 7672
42 7673
42 7674
42 7675
42 7676
42 7677
42 7678
42 7679
42 7680
42 7681
42 7682
42 7683
42 7684
42 7685
42 7686
42 7687


42 8684
42 8685
42 8686
42 8687
42 8688
42 8689
42 8690
42 8691
42 8692
42 8693
42 8694
42 8695
42 8696
42 8697
42 8698
42 8699
42 8700
42 8701
42 8702
42 8703
42 8704
42 8705
42 8706
42 8707
42 8708
42 8709
42 8710
42 8711
42 8712
42 8713
42 8714
42 8715
42 8716
42 8717
42 8718
42 8719
42 8720
42 8721
42 8722
42 8723
42 8724
42 8725
42 8726
42 8727
42 8728
42 8729
42 8730
42 8731
42 8732
42 8733
42 8734
42 8735
42 8736
42 8737
42 8738
42 8739
42 8740
42 8741
42 8742
42 8743
42 8744
42 8745
42 8746
42 8747
42 8748
42 8749
42 8750
42 8751
42 8752
42 8753
42 8754
42 8755
42 8756
42 8757
42 8758
42 8759
42 8760
42 8761
42 8762
42 8763
42 8764
42 8765
42 8766
42 8767
42 8768
42 8769
42 8770
42 8771
42 8772
42 8773
42 8774
42 8775
42 8776
42 8777
42 8778
42 8779
42 8780
42 8781
42 8782
42 8783
42 8784
42 8785
42 8786
42 8787
42 8788
42 8789
42 8790
42 8791
42 8792
42 8793
42 8794
42 8795
42 8796
42 8797
42 8798
42 8799
42 8800
42 8801
42 8802
42 8803
42 8804
42 8805
42 8806
42 8807
42 8808


43 1004
43 1005
43 1006
43 1007
43 1008
43 1009
43 1010
43 1011
43 1012
43 1013
43 1014
43 1015
43 1016
43 1017
43 1018
43 1019
43 1020
43 1021
43 1022
43 1023
43 1024
43 1025
43 1026
43 1027
43 1028
43 1029
43 1030
43 1031
43 1032
43 1033
43 1034
43 1035
43 1036
43 1037
43 1038
43 1039
43 1040
43 1041
43 1042
43 1043
43 1044
43 1045
43 1046
43 1047
43 1048
43 1049
43 1050
43 1051
43 1052
43 1053
43 1054
43 1055
43 1056
43 1057
43 1058
43 1059
43 1060
43 1061
43 1062
43 1063
43 1064
43 1065
43 1066
43 1067
43 1068
43 1069
43 1070
43 1071
43 1072
43 1073
43 1074
43 1075
43 1076
43 1077
43 1078
43 1079
43 1080
43 1081
43 1082
43 1083
43 1084
43 1085
43 1086
43 1087
43 1088
43 1089
43 1090
43 1091
43 1092
43 1093
43 1094
43 1095
43 1096
43 1097
43 1098
43 1099
43 1100
43 1101
43 1102
43 1103
43 1104
43 1105
43 1106
43 1107
43 1108
43 1109
43 1110
43 1111
43 1112
43 1113
43 1114
43 1115
43 1116
43 1117
43 1118
43 1119
43 1120
43 1121
43 1122
43 1123
43 1124
43 1125
43 1126
43 1127
43 1128


43 2839
43 2840
43 2841
43 2842
43 2843
43 2844
43 2845
43 2846
43 2847
43 2848
43 2849
43 2850
43 2851
43 2852
43 2853
43 2854
43 2855
43 2856
43 2857
43 2858
43 2859
43 2860
43 2861
43 2862
43 2863
43 2864
43 2865
43 2866
43 2867
43 2868
43 2869
43 2870
43 2871
43 2872
43 2873
43 2874
43 2875
43 2876
43 2877
43 2878
43 2879
43 2880
43 2881
43 2882
43 2883
43 2884
43 2885
43 2886
43 2887
43 2888
43 2889
43 2890
43 2891
43 2892
43 2893
43 2894
43 2895
43 2896
43 2897
43 2898
43 2899
43 2900
43 2901
43 2902
43 2903
43 2904
43 2905
43 2906
43 2907
43 2908
43 2909
43 2910
43 2911
43 2912
43 2913
43 2914
43 2915
43 2916
43 2917
43 2918
43 2919
43 2920
43 2921
43 2922
43 2923
43 2924
43 2925
43 2926
43 2927
43 2928
43 2929
43 2930
43 2931
43 2932
43 2933
43 2934
43 2935
43 2936
43 2937
43 2938
43 2939
43 2940
43 2941
43 2942
43 2943
43 2944
43 2945
43 2946
43 2947
43 2948
43 2949
43 2950
43 2951
43 2952
43 2953
43 2954
43 2955
43 2956
43 2957
43 2958
43 2959
43 2960
43 2961
43 2962
43 2963


KeyboardInterrupt: 

In [226]:
timetabling = gp.Model("Asignacion de cursos a horarios y salas")

#Conjuntos
C = clases
D = distribuciones
T = tiempos

#Subconjuntos
Tc = dicc_Tc
Sc = dicc_Sc
Wt = dicc_Wt
Ht = dicc_Ht
Dt = dicc_Dt
PTct = dicc_PTct
PScs = dicc_PScs

alfa = int(df_optimization["Time"])
beta = int(df_optimization["Room"])
gamma = int(df_optimization["Distribution"])
delta = int(df_optimization["Student"])

#VARIABLES
x = {} 
for c in clases:
    for t in T:
        x[c,t] = timetabling.addVar(vtype=gp.GRB.BINARY, name='x_'+str(c)+','+str(t))

y = {}
for c in clases:
    for s in Sc[c]:
        y[c,s] = timetabling.addVar(vtype=gp.GRB.BINARY, name='y_'+str(c)+','+str(s))
        
w = {} 
for c in clases:
    for t in T:
        x[c,t] = timetabling.addVar(vtype=gp.GRB.BINARY, name='w_'+str(c)+','+str(t))

d = {} 
for c in clases:
    for t in T:
        x[c,t] = timetabling.addVar(vtype=gp.GRB.BINARY, name='d_'+str(c)+','+str(t))

h  = {} 
for c in clases:
    for t in T:
        x[c,t] = timetabling.addVar(vtype=gp.GRB.BINARY, name='h_'+str(c)+','+str(t))


aux1 = {}
for i in D1:
    aux1[i] = timetabling.addVar(vtype=gp.GRB.BINARY, name="aux1_"+str(i))
    
aux2 = {}
for i in D2:
    aux2[i] = timetabling.addVar(vtype=gp.GRB.BINARY, name="aux2_"+str(i))
    
aux3 = {}
for i in D3:
    aux3[i] = timetabling.addVar(vtype=gp.GRB.BINARY, name="aux3_"+str(i))
    
aux4 = {}
for i in D4:
    aux4[i] = timetabling.addVar(vtype=gp.GRB.BINARY, name="aux4_"+str(i))
    
aux5 = {}
for i in D5:
    aux5[i] = timetabling.addVar(vtype=gp.GRB.BINARY, name="aux5_"+str(i))
    
aux6 = {}
for i in D6:
    aux6[i] = timetabling.addVar(vtype=gp.GRB.BINARY, name="aux6_"+str(i))
    
aux7= {}
for i in D7:
    aux6[i] = timetabling.addVar(vtype=gp.GRB.BINARY, name="aux7_"+str(i))
    
aux8 = {}
for i in D8:
    aux6[i] = timetabling.addVar(vtype=gp.GRB.BINARY, name="aux8_"+str(i))

##FUNCION OBJETIVO
timetabling.setObjective(alfa*gp.quicksum(x[c,t]*PTct[(c,t)] for c in C for t in Tc[c]) + beta*gp.quicksum(y[c,s]*PScs[(c,s)] for c in C for s in Sc[c]),GRB.MINIMIZE)
#timetabling.setObjective(alfa*gp.quicksum(x[c,t]*PT_ct[(c,t)] for c in C for t in TD_c[c]) + beta*gp.quicksum(y[c,s]*PS_cs[(c,s)] for c in C for s in SDisp_c[c]) + gamma*gp.quicksum(aux1[i]*PD_1i[i] for i in I_j[1])+gp.quicksum(aux3[i]*PD_3i[i] for i in I_j[3]) + gp.quicksum(aux4[i]*PD_4i[i] for i in I_j[4]) +delta*gp.quicksum(clash[c1,c2] for c1 in C for c2 in C),GRB.MINIMIZE)

In [227]:
#RESTRICCIONES

In [228]:

#A cada clase se le debe ser asignado un tiempo
timetabling.addConstrs(((gp.quicksum(x[c,t] for t in Tc[c]) == 1) for c in C), name = "R1")

#Cada clase debe ser asignada a una sala (donde sea aplicable)
timetabling.addConstrs(((gp.quicksum(y[c,s] for s in Sc[c]) == 1) for c in C), name = "R2")

#Dos clases no pueden ser asignadas en un mismo tiempo en la misma sala
timetabling.addConstrs(((x[c1,t1] + y[c1,s1] + x[c1,t2] + y[c2,s2] <= 3) for c1 in C for c2 in C for t1 in Tc[c1] for t2 in Tc[c2] for s1 in Sc[c1] for s2 in Sc[c2] if c1 != c2 if  s1 == s2 if t1 == t2), name = "R6")

#Solo debe haber una clase por subparte
#timetabling.addConstrs(((gp.quicksum(x[c,t] for c in dicc_subpartes[p] for t in Tc[c]) == 1) for p in subpartes), name = "Subpartes")

#Distribucion SameStart Dura
timetabling.addConstrs((((h[c1,t1] + h[c2,t2]) == 2) for c1 in C for c2 in C for t1 in Tc[c1] for t2 in Tc[c2] for d in D if Ht[t1] == Ht[t2]  if c1 != c2 if c1 in SS[c2] or c2 in SS[c1]), name = "SameStart")

#Distribucion SameStart Blanda
timetabling.addConstrs(((((h[c1,t1] - h[c2,t2])*(h[c1,t1] - h[c2,t2])) == aux[2,i]) for c1 in C for c2 in C for t1 in Tc[c1] for t2 in Tc[c2] for i in D2 if c1 != c2 if Hc[t1] == Hc[t2] if c1 in SSB[c2] or c2 in SSB[c1]), name = "SameStart B")

#Distribucion SameRoom Dura
timetabling.addConstrs((((y[c1,s1] + y[c2,s2]) == 2) for c1 in C for c2 in C for s1 in SD[c1] for s2 in SD[c2] if c1 != c2 if s1 == s2  if c1 in SR[c2] or c2 in SR[c1]), name = "SameRoom")

#Distribucion SameRoom Blanda
timetabling.addConstrs(((((y[c1,s1] - y[c2,s2])*(y[c1,s1] - y[c2,s2])) == aux[3,i]) for c1 in C for c2 in C for s1 in SD[c1] for s2 in SD[c2] for i in D3 if c1 != c2 if s1 == s2 if c1 in SRB[c2] or c2 in SRB[c1]), name = "SameRoom B")

#Distribucion SameDays Dura
#timetabling.addConstrs((((d[c1,t1] + d[c2,t2]) == 2) for c1 in C for c2 in C for t1 in Tc[c1] for t2 in Tc[c2] if c1 != c2 if Dt[t1] == Dt[t2] if c1 in SD[c2] or c2 in SD[c1] ), name = "SameDays")

#Distribucion SameDays Blanda
timetabling.addConstrs(((((d[c1,t1] - d[c2,t2])*(d[c1,t1] - d[c2,t2])) <= aux[5,i]) for c1 in SD[c1] for c2 in SD[c2] for t1 in Tc[c1] for t2 in Tc[c2] for i in D5 if c1 != c2 if Dt[t1] == Dt[t2] if c1 in SDB[c2] or c2 in SDB[c1]), name = "SameDays B")

#Distribucion SameWeeks Dura
timetabling.addConstrs((((w[c1,t1] + w[c2,t2]) == 2) for c1 in C for c2 in C for t1 in Tc[c1] for t2 in Tc[c2] if c1 != c2 if Wt[t1] == Wt[t2] if c1 in SW[c2] or c2 in SW[c1]), name = "SameWeeks")

#Distribucion SameWeeks Blanda
timetabling.addConstrs(((((w[c1,t1] - w[c2,t2])*(w[c1,t1] - w[c2,t2])) <= aux[6,i]) for c1 in C for c2 in C for t1 in Tc[c1] for t2 in Tc[c2] for i in D5 if c1 != c2 if Wt[t1] == Wt[t2] if c1 in SWB[c2] or c2 in SWB[c1]), name = "SameWeeks B")





timetabling.optimize()


KeyError: (2, 1)

In [ ]:
import csv

varInfo = [(v.varName, int(v.X)) for v in timetabling.getVars() if v.X > 0]

# Write to csv
with open('0.csv', 'w', newline="") as myfile:
    wr = csv.writer(myfile, delimiter = ";", quoting=csv.QUOTE_ALL)
    wr.writerows(varInfo)